In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from datetime import timezone, datetime
from sklearn.preprocessing import OneHotEncoder 
from sklearn.preprocessing import LabelEncoder
#from sklearn.compose import ColumnTransformer 

In [17]:
import csv
import json
from collections import *


class Node(object):
    def __init__(self, depth, code, descr=None):
        self.depth = depth
        self.descr = descr or code
        self.code = code
        self.parent = None
        self.children = []

    def add_child(self, child):
        if child not in self.children:
            self.children.append(child)

    def search(self, code):
        if code == self.code:
            return [self]
        ret = []
        for child in self.children:
            ret.extend(child.search(code))
        return ret

    def find(self, code):
        nodes = self.search(code)
        if nodes:
            return nodes[0]
        return None

    @property
    def root(self):
        return self.parents[0]

    @property
    def description(self):
        return self.descr

    @property
    def codes(self):
        return map(lambda n: n.code, self.leaves)

    @property
    def parents(self):
        n = self
        ret = []
        while n:
            ret.append(n)
            n = n.parent
        ret.reverse()
        return ret

    @property
    def leaves(self):
        leaves = set()
        if not self.children:
            return [self]
        for child in self.children:
            leaves.update(child.leaves)
        return list(leaves)

    # return all leaf notes with a depth of @depth
    def leaves_at_depth(self, depth):
        return filter(lambda n: n.depth == depth, self.leaves)

    @property
    def siblings(self):
        parent = self.parent
        if not parent:
            return []
        return list(parent.children)

    def __str__(self):
        return '%s\t%s' % (self.depth, self.code)

    def __hash__(self):
        return hash(str(self))


class ICD9(Node):
    def __init__(self, codesfname):
        # dictionary of depth -> dictionary of code->node
        self.depth2nodes = defaultdict(dict)
        super(ICD9, self).__init__(-1, 'ROOT')

        with open(codesfname, 'r') as f:
            allcodes = json.loads(f.read())
            self.process(allcodes)

    def process(self, allcodes):
        for hierarchy in allcodes:
            self.add(hierarchy)

    def get_node(self, depth, code, descr):
        d = self.depth2nodes[depth]
        if code not in d:
            d[code] = Node(depth, code, descr)
        return d[code]

    def add(self, hierarchy):
        prev_node = self
        for depth, link in enumerate(hierarchy):
            if not link['code']:
                continue

            code = link['code']
            descr = 'descr' in link and link['descr'] or code
            node = self.get_node(depth, code, descr)
            node.parent = prev_node
            prev_node.add_child(node)
            prev_node = node

In [18]:
# Generate icd9_tree for classification
icd9_tree = ICD9('codes_new.json')
counter = Counter(map(str, icd9_tree.leaves))

In [2]:
#df_pat = pd.read_csv('../data/PATIENTS.csv')
df_diag = pd.read_csv('../data/diagnose_merged.csv')

In [62]:
#df_pat = df_pat.sort_values(by = ['SUBJECT_ID'])
#df_pat = df_pat.set_index(keys = 'ROW_ID', drop = True)
#df_pat.to_csv('../data/patients0.csv')

In [3]:
df_pat = pd.read_csv('../data/patients.csv')
df_pat.head(5)

ROW_ID  SUBJECT_ID GENDER                  DOB                  DOD  \
0     234         249      F  2075-03-13 00:00:00                  NaN   
1     235         250      F  2164-12-27 00:00:00  2188-11-22 00:00:00   
2     236         251      M  2090-03-15 00:00:00                  NaN   
3     237         252      M  2078-03-06 00:00:00                  NaN   
4     238         253      F  2089-11-26 00:00:00                  NaN   

              DOD_HOSP DOD_SSN  EXPIRE_FLAG  
0                  NaN     NaN            0  
1  2188-11-22 00:00:00     NaN            1  
2                  NaN     NaN            0  
3                  NaN     NaN            0  
4                  NaN     NaN            0

In [6]:
df_diag.head(5)

Unnamed: 0  SUBJECT_ID  HADM_ID  SEQ_NUM ICD9_CODE  \
0           0           2   163353      1.0     V3001   
1           1           2   163353      2.0      V053   
2           2           2   163353      3.0      V290   
3           3           3   145834      9.0      2639   
4           4           3   145834      7.0      6826   

                SHORT_TITLE                                         LONG_TITLE  
0    Single lb in-hosp w cs  Single liveborn, born in hospital, delivered b...  
1  Need prphyl vc vrl hepat  Need for prophylactic vaccination and inoculat...  
2    NB obsrv suspct infect     Observation for suspected infectious condition  
3   Protein-cal malnutr NOS           Unspecified protein-calorie malnutrition  
4         Cellulitis of leg         Cellulitis and abscess of leg, except foot

In [65]:
len(df_diag)

651047

In [66]:
df_diag['Diabetes'] = df_diag['ICD9_CODE'].apply(lambda x: str(x)[0:3] == '250')

In [67]:
df_diabete = df_diag[df_diag['Diabetes'] == True]

In [68]:
len(df_diabete)
print('Percentage of Diabetes diagnosis: '+str(len(df_diabete)/len(df_diag)))
print('Unique number of diabetes patients: '+ str(len(df_diabete['SUBJECT_ID'].unique())))

Percentage of Diabetes diagnosis: 0.025273136962462004
Unique number of diabetes patients: 10318


In [50]:
df_diabete.tail(30)

Unnamed: 0  SUBJECT_ID  HADM_ID  SEQ_NUM ICD9_CODE  \
650148      650148       99802   108099      5.0     25000   
650163      650163       99806   133851      4.0     25080   
650167      650167       99809   154672      5.0     25000   
650180      650180       99810   196261      7.0     25000   
650184      650184       99814   186518      4.0     25000   
650223      650223       99819   126883     10.0     25000   
650297      650297       99830   176834     22.0     25000   
650436      650436       99863   100749      7.0     25012   
650452      650452       99864   111512     11.0     25040   
650514      650514       99870   124555      9.0     25060   
650586      650586       99893   128349     15.0     25050   
650626      650626       99897   181057      7.0     25062   
650627      650627       99897   181057      9.0     25052   
650629      650629       99897   181057     11.0     25042   
650633      650633       99897   181057      1.0     25012   
650640      650640       99897   162913      1.0     25020   
650649      650649       99897   162913     11.0     25040   
650650      650650       99897   162913     12.0     25050   
650651      650651       99897   162913     13.0     25060   
650659      650659       99899   188409     19.0     25000   
650695      650695       99901   131711      6.0     25000   
650710      650710       99903   135939      4.0     25000   
650738      650738       99913   175989     10.0     25000   
650782      650782       99928   104802      1.0     25013   
650829      650829       99938   103815      6.0     25000   
650892      650892       99955   108494      6.0     25060   
650907      650907       99957   148574     11.0     25092   
651006      651006       99991   151118     14.0     25000   
651032      651032       99995   137810      6.0     25000   
651042      651042       99999   113369      4.0     25000   

                     SHORT_TITLE  \
650148  DMII wo cmp nt st uncntr   
650163   DMII oth nt st uncntrld   
650167  DMII wo cmp nt st uncntr   
650180  DMII wo cmp nt st uncntr   
650184  DMII wo cmp nt st uncntr   
650223  DMII wo cmp nt st uncntr   
650297  DMII wo cmp nt st uncntr   
650436   DMII ketoacd uncontrold   
650452  DMII renl nt st uncntrld   
650514  DMII neuro nt st uncntrl   
650586  DMII ophth nt st uncntrl   
650626       DMII neuro uncntrld   
650627       DMII ophth uncntrld   
650629       DMII renal uncntrld   
650633   DMII ketoacd uncontrold   
650640  DMII hprsm nt st uncntrl   
650649  DMII renl nt st uncntrld   
650650  DMII ophth nt st uncntrl   
650651  DMII neuro nt st uncntrl   
650659  DMII wo cmp nt st uncntr   
650695  DMII wo cmp nt st uncntr   
650710  DMII wo cmp nt st uncntr   
650738  DMII wo cmp nt st uncntr   
650782    DMI ketoacd uncontrold   
650829  DMII wo cmp nt st uncntr   
650892  DMII neuro nt st uncntrl   
650907       DMII unspf uncntrld   
651006  DMII wo cmp nt st uncntr   
651032  DMII wo cmp nt st uncntr   
651042  DMII wo cmp nt st uncntr   

                                               LONG_TITLE  Diabetes  
650148  Diabetes mellitus without mention of complicat...      True  
650163  Diabetes with other specified manifestations, ...      True  
650167  Diabetes mellitus without mention of complicat...      True  
650180  Diabetes mellitus without mention of complicat...      True  
650184  Diabetes mellitus without mention of complicat...      True  
650223  Diabetes mellitus without mention of complicat...      True  
650297  Diabetes mellitus without mention of complicat...      True  
650436  Diabetes with ketoacidosis, type II or unspeci...      True  
650452  Diabetes with renal manifestations, type II or...      True  
650514  Diabetes with neurological manifestations, typ...      True  
650586  Diabetes with ophthalmic manifestations, type ...      True  
650626  Diabetes with neurological manifestations, typ...      True  
650627  Diabetes with ophthalmic manifestations, type ... 

In [75]:
pat_name = list(df_diabete['SUBJECT_ID'].unique())
pat_name

[13,
 18,
 20,
 21,
 24,
 25,
 28,
 35,
 37,
 55,
 59,
 75,
 83,
 117,
 123,
 130,
 135,
 137,
 141,
 157,
 173,
 184,
 186,
 188,
 191,
 192,
 199,
 205,
 209,
 210,
 224,
 234,
 235,
 239,
 246,
 249,
 261,
 263,
 270,
 271,
 286,
 294,
 305,
 309,
 321,
 323,
 328,
 342,
 344,
 345,
 347,
 352,
 353,
 354,
 357,
 359,
 367,
 370,
 376,
 378,
 379,
 382,
 383,
 389,
 395,
 402,
 415,
 427,
 430,
 445,
 450,
 452,
 453,
 454,
 464,
 482,
 485,
 489,
 494,
 501,
 511,
 518,
 527,
 532,
 533,
 539,
 545,
 558,
 563,
 564,
 565,
 569,
 571,
 584,
 588,
 609,
 613,
 622,
 624,
 629,
 630,
 634,
 635,
 641,
 642,
 654,
 666,
 667,
 671,
 672,
 689,
 690,
 702,
 703,
 708,
 711,
 715,
 716,
 720,
 732,
 741,
 745,
 747,
 751,
 756,
 757,
 765,
 770,
 772,
 780,
 787,
 791,
 794,
 798,
 806,
 811,
 816,
 820,
 824,
 834,
 835,
 837,
 846,
 849,
 864,
 865,
 876,
 890,
 894,
 906,
 914,
 919,
 921,
 923,
 924,
 925,
 929,
 932,
 940,
 946,
 947,
 954,
 956,
 963,
 979,
 984,
 989,
 992,
 995,

In [79]:
diabete_patients = df_pat[df_pat['SUBJECT_ID'].isin(pat_name)]

In [70]:
diabete_patients

Unnamed: 0  ROW_ID  SUBJECT_ID GENDER                  DOB  \
0              11      12          13      F  2127-02-27 00:00:00   
1              14      15          18      M  2116-11-29 00:00:00   
2              16      17          20      F  2107-06-13 00:00:00   
3              17      18          21      M  2047-04-04 00:00:00   
4              20      21          24      M  2100-05-31 00:00:00   
5              21      22          25      M  2101-11-21 00:00:00   
6              24      25          28      M  2103-04-15 00:00:00   
7              30      31          35      F  2052-09-01 00:00:00   
8              32      33          37      M  2114-09-17 00:00:00   
9              47      48          55      F  2072-02-04 00:00:00   
10             51      52          59      F  2110-10-12 00:00:00   
11             67      68          75      F  2070-06-27 00:00:00   
12             74      75          83      F  2076-09-15 00:00:00   
13            107     108         117      F  2083-12-28 00:00:00   
14            112     113         123      M  2105-08-31 00:00:00   
15            119     120         130      M  2058-06-03 00:00:00   
16            124     125         135      M  2123-06-09 00:00:00   
17            126     127         137      M  2117-02-27 00:00:00   
18            130     131         141      M  2060-05-03 00:00:00   
19            146     147         157      M  2025-12-03 00:00:00   
20            162     163         173      F  2045-08-06 00:00:00   
21            173     174         184      M  2111-10-16 00:00:00   
22            175     176         186      F  2100-12-05 00:00:00   
23            177     178         188      M  2105-05-18 00:00:00   
24            180     181         191      M  2123-02-12 00:00:00   
25            181     182         192      M  2066-07-27 00:00:00   
26            187     188         199      M  2125-10-12 00:00:00   
27            193     194         205      F  2116-07-25 00:00:00   
28            195     196         209      M  2054-01-13 00:00:00   
29            196     197         210      F  2064-05-03 00:00:00   
...           ...     ...         ...    ...                  ...   
10288       46423   46424       99629      M  2113-04-18 00:00:00   
10289       46429   46430       99650      F  2101-07-10 00:00:00   
10290       46432   46433       99660      F  2067-02-23 00:00:00   
10291       46443   46444       99714      M  2043-12-06 00:00:00   
10292       46450   46451       99756      M  2140-01-06 00:00:00   
10293       46454   46455       99776      M  2115-02-01 00:00:00   
10294       46460   46461       99791      M  2109-01-04 00:00:00   
10295       46463   46464       99802      F  2039-09-10 00:00:00   
10296       46464   46465       99806      M  2041-04-11 00:00:00   
10297       46465   46466       99809      M  2096-03-03 00:00:00   
10298       46466   46467       99810      M  2051-05-25 00:00:00   
10299       46467   46468       99814      F  2055-07-17 00:00:00   
10300       46469   46470       99819      M  2066-11-28 00:00:00   
10301       46472   46473       99830      M  2138-05-11 00:00:00   
10302       46479   46480       99863      M  2099-07-23 00:00:00   
10303       46480   46481       99864      M  2045-03-13 00:00:00   
10304       46483   46484       99870      F  2123-01-29 00:00:00   
10305       46489   46490       99893      M  2104-09-12 00:00:00   
10306       46491   46492       99897      M  2128-01-18 00:00:00   
10307       46492   46493       99899      M  2026-06-20 00:00:00   
10308       46493   46494       99901      M  2104-03-10 00:00:00   
10309       46494   46495       99903      M  2095-11-27 00:00:00   
10310       46496   46497       99913      M  2070-04-07 00:00:00   
10311       46499   46500       99928      F  2161-01-02 00:00:00   
10312       46504   46505       99938      M  2119-12-23 00:00:00   
10313       46508   46509       99955      M  2076-05-04 00:00:00   
10314

In [81]:
id_lst = list(diabete_patients['SUBJECT_ID'])
diag_lst = []
descrip_lst = []
seq_lst = []
hadm_lst =[]
for i in id_lst:
    d = df_diag[df_diag['SUBJECT_ID']==i]
    this_diag = list(d['ICD9_CODE'])
    this_des = list(d['LONG_TITLE'])
    this_seq = list(d['SEQ_NUM'])
    this_hadm = list(d['HADM_ID'])
    diag_lst.append(this_diag)
    descrip_lst.append(this_des)
    seq_lst.append(this_seq)
    hadm_lst.append(this_hadm)

In [86]:
diabete_patients['DIAGNOSES'] = descrip_lst
diabete_patients['ICD9_CODE'] = diag_lst
diabete_patients['SEQ_NUM'] = seq_lst
diabete_patients['HADM_ID'] = hadm_lst

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/p

In [7]:
diabete_patients = pd.read_csv('../data/diabetes_patients.csv')
#diabete_patients.to_csv(r'/Users/rayeliu/Desktop/mimic3-research/data/diabetes_patients.csv')

In [8]:
diabete_patients.head(20)

Unnamed: 0  ROW_ID  SUBJECT_ID GENDER                  DOB  \
0           11      12          13      F  2127-02-27 00:00:00   
1           14      15          18      M  2116-11-29 00:00:00   
2           16      17          20      F  2107-06-13 00:00:00   
3           17      18          21      M  2047-04-04 00:00:00   
4           20      21          24      M  2100-05-31 00:00:00   
5           21      22          25      M  2101-11-21 00:00:00   
6           24      25          28      M  2103-04-15 00:00:00   
7           30      31          35      F  2052-09-01 00:00:00   
8           32      33          37      M  2114-09-17 00:00:00   
9           47      48          55      F  2072-02-04 00:00:00   
10          51      52          59      F  2110-10-12 00:00:00   
11          67      68          75      F  2070-06-27 00:00:00   
12          74      75          83      F  2076-09-15 00:00:00   
13         107     108         117      F  2083-12-28 00:00:00   
14         112     113         123      M  2105-08-31 00:00:00   
15         119     120         130      M  2058-06-03 00:00:00   
16         124     125         135      M  2123-06-09 00:00:00   
17         126     127         137      M  2117-02-27 00:00:00   
18         130     131         141      M  2060-05-03 00:00:00   
19         146     147         157      M  2025-12-03 00:00:00   

                    DOD             DOD_HOSP              DOD_SSN  \
0                   NaN                  NaN                  NaN   
1                   NaN                  NaN                  NaN   
2                   NaN                  NaN                  NaN   
3   2135-02-08 00:00:00  2135-02-08 00:00:00  2135-02-08 00:00:00   
4                   NaN                  NaN                  NaN   
5                   NaN                  NaN                  NaN   
6                   NaN                  NaN                  NaN   
7                   NaN                  NaN                  NaN   
8   2185-01-06 00:00:00  2185-01-06 00:00:00  2185-01-06 00:00:00   
9                   NaN                  NaN                  NaN   
10  2198-09-06 00:00:00  2198-09-06 00:00:00  2198-09-06 00:00:00   
11                  NaN                  NaN                  NaN   
12  2142-11-20 00:00:00                  NaN  2142-11-20 00:00:00   
13  2133-12-01 00:00:00  2133-12-01 00:00:00  2133-12-01 00:00:00   
14                  NaN                  NaN                  NaN   
15  2120-04-15 00:00:00  2120-04-15 00:00:00                  NaN   
16  2175-12-16 00:00:00                  NaN  2175-12-16 00:00:00   
17  2193-05-15 00:00:00                  NaN  2193-05-15 00:00:00   
18  2140-11-09 00:00:00  2140-11-09 00:00:00  2140-11-09 00:00:00   
19  2106-08-25 00:00:00                  NaN  2106-08-25 00:00:00   

    EXPIRE_FLAG                                          DIAGNOSES  \
0             0  ['Pure hypercholesterolemia', 'Unspecified ess...   
1             0  ['Pure hypercholesterolemia', 'Right bundle br...   
2             0  ['Coronary atherosclerosis of native coronary ...   
3             1  ['Abscess of liver', 'Intestinal infection due...   
4             0  ['Diabetes mellitus without mention of complic...   
5             0  ['Unspecified essential hypertension', 'Corona...   
6             0  ['Other isolated or specific phobias', nan, 'P...   
7             0  ['Osteoarthrosis, unspecified whether generali...   
8             1  ['Subendocardial infarction, initial episode o...   
9             0  ['Occlusion and stenosis of carotid artery wit...   
10            1  ['Hypotension, unspecified', 'Urinary tract in...   
11            0  ['Diabetes mellitus without mention of complic...   
12            1  ['Hypertensive chronic kidney disease, unspeci...   
13            1  ['Acute posthemorrhagic anemia', 'Cirrhosis of...   
14            0  ['Unspecified essential hypertension', 'Acute ...   
15            1  ['Pure hypercholesterolemia', 

In [9]:
len(df_diag['ICD9_CODE'].unique())

6985

In [46]:
df_subject = diabete_patients.iloc[:, [2, 3, 9, 10, 11, 12]]
df_subject

SUBJECT_ID GENDER                                          DIAGNOSES  \
0              13      F  ['Pure hypercholesterolemia', 'Unspecified ess...   
1              18      M  ['Pure hypercholesterolemia', 'Right bundle br...   
2              20      F  ['Coronary atherosclerosis of native coronary ...   
3              21      M  ['Abscess of liver', 'Intestinal infection due...   
4              24      M  ['Diabetes mellitus without mention of complic...   
5              25      M  ['Unspecified essential hypertension', 'Corona...   
6              28      M  ['Other isolated or specific phobias', nan, 'P...   
7              35      F  ['Osteoarthrosis, unspecified whether generali...   
8              37      M  ['Subendocardial infarction, initial episode o...   
9              55      F  ['Occlusion and stenosis of carotid artery wit...   
10             59      F  ['Hypotension, unspecified', 'Urinary tract in...   
11             75      F  ['Diabetes mellitus without mention of complic...   
12             83      F  ['Hypertensive chronic kidney disease, unspeci...   
13            117      F  ['Acute posthemorrhagic anemia', 'Cirrhosis of...   
14            123      M  ['Unspecified essential hypertension', 'Acute ...   
15            130      M  ['Pure hypercholesterolemia', 'Polyneuropathy ...   
16            135      M  ['Diabetes mellitus without mention of complic...   
17            137      M  ['Personal history of tobacco use', 'Percutane...   
18            141      M  ['Diabetes with ketoacidosis, type I [juvenile...   
19            157      M  ['Hypopotassemia', nan, 'Unspecified essential...   
20            173      F  ['Unspecified sleep apnea', 'Coronary atherosc...   
21            184      M  [nan, 'Pneumonia, organism unspecified', nan, ...   
22            186      F  ['Esophageal varices with bleeding', 'Pneumoni...   
23            188      M  ['Surgical operation with transplant of whole ...   
24            191      M  ['Iron deficiency anemia secondary to blood lo...   
25            192      M  ['Peripheral vascular disease, unspecified', '...   
26            199      M  ['Polyneuropathy in diabetes', 'Congestive hea...   
27            205      F  ['Old myocardial infarction', 'Diabetes mellit...   
28            209      M  ['Hyperpotassemia', 'Diabetes with other speci...   
29            210      F  ['Esophageal reflux', 'Other and unspecified h...   
...           ...    ...                                                ...   
10288       99629      M  ['Esophageal reflux', 'Other and unspecified h...   
10289       99650      F  ['Anemia of other chronic disease', 'Extrinsic...   
10290       99660      F  [nan, 'Chronic kidney disease, Stage IV (sever...   
10291       99714      M  ['Unspecified glaucoma', 'Essential and other ...   
10292       99756      M  ['Thrombocytopenia, unspecified', 'Hyposmolali...   
10293       99776      M  ['Encephalopathy, unspecified', 'Unspecified p...   
10294       99791      M  ['Calculus of bile duct with other cholecystit...   
10295       99802      F  ['Chronic airway obstruction, not elsewhere cl...   
10296       99806      M  ['Other postoperative infection', 'Cellulitis ...   
10297       99809      M  ['Coronary atherosclerosis of native coronary ...   
10298       99810      M  ['Urinary complications, not elsewhere classif...   
10299       99814      F  ['Other toe(s) amputation status', 'Urinary tr...   
10300       99819      M  ['Other and unspecified hyperlipidemia', 'Card...   
10301       99830      M  ['Personal history of sudden cardiac arrest', ...   
10302       99863      M  ['Other and unspecified hyperlipidemia', 'Acut...   
10303       99864      M  ['Chronic kidney disease, Stage III (moderate)...   
10304       99870      F  ['Obstructive sleep apnea (adult)(pediatric)',...   
10305       99893      M  ['Syncope and collapse', 'Accidental fall from...   
10306       99897      M  ['Polyneuropathy in diabetes', 

In [27]:
ICD_list = []
for i in range(1,1000):
    code = str(i)
    if len(code) == 1:
        ICD_list.append('00'+code)
    elif len(code) == 2:
        ICD_list.append('0'+code)
    else:
        ICD_list.append(code)

In [29]:
for i in range(800, 1000):
    ICD_list.append('E' + str(i))

In [36]:
for i in range(1, 83):
    code = str(i)
    if len(code) ==1:
        ICD_list.append('V0' + code)
    else:
        ICD_list.append('V' + code)

In [39]:
for i in range(8000, 9971):
    ICD_list.append('M' + str(i))

In [44]:
pat_num = len(diabete_patients)
pat_num

10318

In [47]:
for cd in ICD_list:
    df_subject[cd] = [0]*pat_num

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [49]:
df_subject.head(5)

SUBJECT_ID GENDER                                          DIAGNOSES  \
0          13      F  ['Pure hypercholesterolemia', 'Unspecified ess...   
1          18      M  ['Pure hypercholesterolemia', 'Right bundle br...   
2          20      F  ['Coronary atherosclerosis of native coronary ...   
3          21      M  ['Abscess of liver', 'Intestinal infection due...   
4          24      M  ['Diabetes mellitus without mention of complic...   

                                           ICD9_CODE  \
0         ['2720', '4019', '4111', '41401', '25000']   
1  ['2720', '4264', '4019', '78321', '78057', '47...   
2         ['41401', '4111', '25000', '2724', '4019']   
3  ['5720', '00845', '70709', '6823', '5119', '99...   
4               ['25000', '41401', '41041', '53081']   

                                             SEQ_NUM  \
0                          [5.0, 4.0, 2.0, 1.0, 3.0]   
1  [12.0, 11.0, 10.0, 9.0, 8.0, 7.0, 13.0, 4.0, 3...   
2                          [1.0, 2.0, 3.0, 4.0, 5.0]   
3  [10.0, 9.0, 5.0, 7.0, 6.0, 11.0, 8.0, 12.0, 4....   
4                               [4.0, 2.0, 1.0, 3.0]   

                                             HADM_ID  001  002  003  004  \
0           [143045, 143045, 143045, 143045, 143045]    0    0    0    0   
1  [188822, 188822, 188822, 188822, 188822, 18882...    0    0    0    0   
2           [157681, 157681, 157681, 157681, 157681]    0    0    0    0   
3  [111970, 111970, 111970, 111970, 111970, 11197...    0    0    0    0   
4                   [161859, 161859, 161859, 161859]    0    0    0    0   

   ...    M9961  M9962  M9963  M9964  M9965  M9966  M9967  M9968  M9969  M9970  
0  ...        0      0      0      0      0      0      0      0      0      0  
1  ...        0      0      0      0      0      0      0      0      0      0  
2  ...        0      0      0      0      0      0      0      0      0      0  
3  ...        0      0      0      0      0      0      0      0      0      0  
4  ...        0      0      0      0      0      0      0      0      0      0  

[5 rows x 3258 columns]

In [79]:
p3 = df_subject.copy()

In [58]:
p3

SUBJECT_ID GENDER                                          DIAGNOSES  \
0              13      F  ['Pure hypercholesterolemia', 'Unspecified ess...   
1              18      M  ['Pure hypercholesterolemia', 'Right bundle br...   
2              20      F  ['Coronary atherosclerosis of native coronary ...   
3              21      M  ['Abscess of liver', 'Intestinal infection due...   
4              24      M  ['Diabetes mellitus without mention of complic...   
5              25      M  ['Unspecified essential hypertension', 'Corona...   
6              28      M  ['Other isolated or specific phobias', nan, 'P...   
7              35      F  ['Osteoarthrosis, unspecified whether generali...   
8              37      M  ['Subendocardial infarction, initial episode o...   
9              55      F  ['Occlusion and stenosis of carotid artery wit...   
10             59      F  ['Hypotension, unspecified', 'Urinary tract in...   
11             75      F  ['Diabetes mellitus without mention of complic...   
12             83      F  ['Hypertensive chronic kidney disease, unspeci...   
13            117      F  ['Acute posthemorrhagic anemia', 'Cirrhosis of...   
14            123      M  ['Unspecified essential hypertension', 'Acute ...   
15            130      M  ['Pure hypercholesterolemia', 'Polyneuropathy ...   
16            135      M  ['Diabetes mellitus without mention of complic...   
17            137      M  ['Personal history of tobacco use', 'Percutane...   
18            141      M  ['Diabetes with ketoacidosis, type I [juvenile...   
19            157      M  ['Hypopotassemia', nan, 'Unspecified essential...   
20            173      F  ['Unspecified sleep apnea', 'Coronary atherosc...   
21            184      M  [nan, 'Pneumonia, organism unspecified', nan, ...   
22            186      F  ['Esophageal varices with bleeding', 'Pneumoni...   
23            188      M  ['Surgical operation with transplant of whole ...   
24            191      M  ['Iron deficiency anemia secondary to blood lo...   
25            192      M  ['Peripheral vascular disease, unspecified', '...   
26            199      M  ['Polyneuropathy in diabetes', 'Congestive hea...   
27            205      F  ['Old myocardial infarction', 'Diabetes mellit...   
28            209      M  ['Hyperpotassemia', 'Diabetes with other speci...   
29            210      F  ['Esophageal reflux', 'Other and unspecified h...   
...           ...    ...                                                ...   
10288       99629      M  ['Esophageal reflux', 'Other and unspecified h...   
10289       99650      F  ['Anemia of other chronic disease', 'Extrinsic...   
10290       99660      F  [nan, 'Chronic kidney disease, Stage IV (sever...   
10291       99714      M  ['Unspecified glaucoma', 'Essential and other ...   
10292       99756      M  ['Thrombocytopenia, unspecified', 'Hyposmolali...   
10293       99776      M  ['Encephalopathy, unspecified', 'Unspecified p...   
10294       99791      M  ['Calculus of bile duct with other cholecystit...   
10295       99802      F  ['Chronic airway obstruction, not elsewhere cl...   
10296       99806      M  ['Other postoperative infection', 'Cellulitis ...   
10297       99809      M  ['Coronary atherosclerosis of native coronary ...   
10298       99810      M  ['Urinary complications, not elsewhere classif...   
10299       99814      F  ['Other toe(s) amputation status', 'Urinary tr...   
10300       99819      M  ['Other and unspecified hyperlipidemia', 'Card...   
10301       99830      M  ['Personal history of sudden cardiac arrest', ...   
10302       99863      M  ['Other and unspecified hyperlipidemia', 'Acut...   
10303       99864      M  ['Chronic kidney disease, Stage III (moderate)...   
10304       99870      F  ['Obstructive sleep apnea (adult)(pediatric)',...   
10305       99893      M  ['Syncope and collapse', 'Accidental fall from...   
10306       99897      M  ['Polyneuropathy in diabetes', 

In [76]:
lst = p3.iloc[0]['ICD9_CODE'][1:-1].split(', ')

In [78]:
lst[1][1:-1]

'4019'

In [80]:
for i in range(pat_num):
    print('Iteration: '+str(i))
    this_pat = p3.iloc[i]['SUBJECT_ID']
    this_code = p3.iloc[i]['ICD9_CODE'][1:-1].split(', ')
    for cd in this_code:
        cd = cd[1:-1]
        if cd[0] == 'E':
            cd = cd[0:4]
        elif cd[0] == 'M':
            cd = cd[0:5]
        else:
            cd = cd[0:3]
        p3.at[i, str(cd)] = 1
        if str(cd) != 'nan':
            print('Patient '+str(this_pat)+', '+ str(cd) + ': '+str(p3.iloc[i][cd]))

Iteration: 0
Patient 13, 272: 1
Patient 13, 401: 1
Patient 13, 411: 1
Patient 13, 414: 1
Patient 13, 250: 1
Iteration: 1
Patient 18, 272: 1
Patient 18, 426: 1
Patient 18, 401: 1
Patient 18, 783: 1
Patient 18, 780: 1
Patient 18, 478: 1
Patient 18, V17: 1
Patient 18, V58: 1
Patient 18, 296: 1
Patient 18, 780: 1
Patient 18, 250: 1
Patient 18, V58: 1
Patient 18, E932: 1
Iteration: 2
Patient 20, 414: 1
Patient 20, 411: 1
Patient 20, 250: 1
Patient 20, 272: 1
Patient 20, 401: 1
Iteration: 3
Patient 21, 572: 1
Patient 21, 008: 1
Patient 21, 707: 1
Patient 21, 682: 1
Patient 21, 511: 1
Patient 21, 995: 1
Patient 21, 998: 1
Patient 21, V09: 1
Patient 21, 427: 1
Patient 21, 285: 1
Patient 21, 438: 1
Patient 21, 274: 1
Patient 21, 414: 1
Patient 21, 185: 1
Patient 21, 443: 1
Patient 21, 244: 1
Patient 21, E878: 1
Patient 21, 250: 1
Patient 21, 403: 1
Patient 21, 250: 1
Patient 21, 038: 1
Patient 21, 785: 1
Patient 21, 785: 1
Patient 21, 578: 1
Patient 21, 584: 1
Patient 21, 403: 1
Patient 21, 428

Patient 199, 424: 1
Patient 199, 493: 1
Patient 199, 278: 1
Patient 199, 424: 1
Patient 199, 427: 1
Patient 199, 785: 1
Patient 199, 414: 1
Patient 199, 428: 1
Patient 199, 427: 1
Patient 199, 428: 1
Patient 199, 410: 1
Patient 199, 414: 1
Patient 199, 500: 1
Iteration: 27
Patient 205, 412: 1
Patient 205, 250: 1
Patient 205, 285: 1
Patient 205, 414: 1
Patient 205, 599: 1
Patient 205, 276: 1
Patient 205, 424: 1
Patient 205, 428: 1
Patient 205, 458: 1
Iteration: 28
Patient 209, 276: 1
Patient 209, 250: 1
Patient 209, V58: 1
Patient 209, 287: 1
Patient 209, 428: 1
Patient 209, 600: 1
Patient 209, 285: 1
Patient 209, V45: 1
Patient 209, 272: 1
Patient 209, 496: 1
Patient 209, V49: 1
Patient 209, V45: 1
Patient 209, V10: 1
Patient 209, 414: 1
Patient 209, V45: 1
Patient 209, V49: 1
Patient 209, 428: 1
Patient 209, 428: 1
Patient 209, 250: 1
Patient 209, 424: 1
Patient 209, 996: 1
Patient 209, 414: 1
Patient 209, 410: 1
Patient 209, 250: 1
Patient 209, 285: 1
Patient 209, V45: 1
Patient 209,

Patient 352, 412: 1
Patient 352, V12: 1
Patient 352, 250: 1
Patient 352, 401: 1
Patient 352, 434: 1
Patient 352, 414: 1
Patient 352, 440: 1
Patient 352, 496: 1
Patient 352, 444: 1
Patient 352, 428: 1
Patient 352, 440: 1
Patient 352, 285: 1
Patient 352, 593: 1
Patient 352, 745: 1
Patient 352, V45: 1
Patient 352, 250: 1
Patient 352, 274: 1
Patient 352, 272: 1
Patient 352, 401: 1
Patient 352, V12: 1
Patient 352, V45: 1
Patient 352, 414: 1
Patient 352, 433: 1
Patient 352, V58: 1
Iteration: 52
Patient 353, 577: 1
Patient 353, 424: 1
Patient 353, 428: 1
Patient 353, 250: 1
Patient 353, 585: 1
Patient 353, 996: 1
Patient 353, 995: 1
Patient 353, 038: 1
Patient 353, V49: 1
Patient 353, 362: 1
Patient 353, 403: 1
Patient 353, V45: 1
Patient 353, 996: 1
Patient 353, V58: 1
Patient 353, 285: 1
Patient 353, 250: 1
Patient 353, 790: 1
Patient 353, 707: 1
Patient 353, 427: 1
Patient 353, 428: 1
Patient 353, 428: 1
Patient 353, 511: 1
Patient 353, 997: 1
Patient 353, 427: 1
Patient 353, 348: 1
Patien

Patient 452, 303: 1
Patient 452, 530: 1
Patient 452, 273: 1
Patient 452, 348: 1
Patient 452, V58: 1
Patient 452, 250: 1
Patient 452, 574: 1
Patient 452, 528: 1
Patient 452, 729: 1
Patient 452, 486: 1
Patient 452, 518: 1
Patient 452, 401: 1
Patient 452, 263: 1
Patient 452, 571: 1
Patient 452, 564: 1
Patient 452, 287: 1
Patient 452, 570: 1
Patient 452, 276: 1
Patient 452, 785: 1
Patient 452, 584: 1
Patient 452, 995: 1
Patient 452, 038: 1
Patient 452, V10: 1
Patient 452, 507: 1
Patient 452, 518: 1
Patient 452, 255: 1
Patient 452, 276: 1
Patient 452, 428: 1
Patient 452, 263: 1
Patient 452, 276: 1
Patient 452, V42: 1
Iteration: 72
Patient 453, V66: 1
Patient 453, 250: 1
Patient 453, 403: 1
Patient 453, 507: 1
Patient 453, 396: 1
Patient 453, 398: 1
Patient 453, 421: 1
Patient 453, 790: 1
Patient 453, 320: 1
Iteration: 73
Patient 454, 369: 1
Patient 454, 305: 1
Patient 454, 364: 1
Patient 454, 278: 1
Patient 454, 250: 1
Patient 454, 427: 1
Patient 454, 342: 1
Patient 454, V12: 1
Patient 454,

Patient 634, 789: 1
Patient 634, 999: 1
Patient 634, 482: 1
Patient 634, 286: 1
Patient 634, 518: 1
Patient 634, 285: 1
Patient 634, 785: 1
Patient 634, 531: 1
Patient 634, 572: 1
Patient 634, 518: 1
Patient 634, 280: 1
Patient 634, 592: 1
Patient 634, 785: 1
Patient 634, 730: 1
Patient 634, 403: 1
Patient 634, 593: 1
Patient 634, 401: 1
Patient 634, 250: 1
Patient 634, 285: 1
Patient 634, 576: 1
Patient 634, 458: 1
Patient 634, 276: 1
Patient 634, 276: 1
Patient 634, 285: 1
Patient 634, 737: 1
Patient 634, 733: 1
Patient 634, 588: 1
Patient 634, 263: 1
Patient 634, 578: 1
Patient 634, 599: 1
Patient 634, 008: 1
Patient 634, 584: 1
Patient 634, 518: 1
Patient 634, 722: 1
Patient 634, 733: 1
Patient 634, 570: 1
Patient 634, 507: 1
Patient 634, 996: 1
Patient 634, 996: 1
Patient 634, 996: 1
Patient 634, 250: 1
Patient 634, 571: 1
Patient 634, 286: 1
Iteration: 102
Patient 635, 250: 1
Patient 635, 295: 1
Patient 635, 576: 1
Patient 635, 414: 1
Iteration: 103
Patient 641, 440: 1
Patient 64

...

Patient 98697, V43: 1
Patient 98697, 401: 1
Patient 98697, 799: 1
Patient 98697, 250: 1
Patient 98697, 440: 1
Patient 98697, 496: 1
Patient 98697, 414: 1
Patient 98697, 428: 1
Patient 98697, 518: 1
Patient 98697, 486: 1
Patient 98697, 441: 1
Iteration: 10232
Patient 98713, 410: 1
Patient 98713, 414: 1
Patient 98713, 250: 1
Patient 98713, 401: 1
Patient 98713, 272: 1
Iteration: 10233
Patient 98733, 276: 1
Patient 98733, 414: 1
Patient 98733, 250: 1
Patient 98733, 250: 1
Patient 98733, 585: 1
Patient 98733, 357: 1
Patient 98733, 403: 1
Patient 98733, 272: 1
Patient 98733, 362: 1
Patient 98733, 459: 1
Patient 98733, 997: 1
Patient 98733, 285: 1
Patient 98733, E878: 1
Patient 98733, 715: 1
Patient 98733, 413: 1
Patient 98733, 692: 1
Patient 98733, 427: 1
Iteration: 10234
Patient 98749, 285: 1
Patient 98749, 276: 1
Patient 98749, 275: 1
Patient 98749, 250: 1
Patient 98749, 584: 1
Iteration: 10235
Patient 98751, 300: 1
Patient 98751, 733: 1
Patient 98751, 276: 1
Patient 98751, V43: 1
Patient

Patient 99260, 348: 1
Patient 99260, 250: 1
Patient 99260, 585: 1
Patient 99260, 403: 1
Patient 99260, 276: 1
Patient 99260, 428: 1
Patient 99260, 261: 1
Patient 99260, 327: 1
Patient 99260, 322: 1
Patient 99260, 585: 1
Iteration: 10258
Patient 99268, V58: 1
Patient 99268, V69: 1
Patient 99268, 787: 1
Patient 99268, 198: 1
Patient 99268, 198: 1
Patient 99268, 788: 1
Patient 99268, 458: 1
Patient 99268, 345: 1
Patient 99268, 511: 1
Patient 99268, 112: 1
Patient 99268, 197: 1
Patient 99268, 250: 1
Patient 99268, 196: 1
Patient 99268, 197: 1
Patient 99268, 197: 1
Patient 99268, 198: 1
Patient 99268, 599: 1
Patient 99268, 348: 1
Patient 99268, 348: 1
Patient 99268, 198: 1
Patient 99268, V10: 1
Patient 99268, 197: 1
Patient 99268, V86: 1.0
Patient 99268, 197: 1
Patient 99268, 346: 1
Patient 99268, 197: 1
Patient 99268, 196: 1
Patient 99268, 599: 1
Patient 99268, 198: 1
Patient 99268, V58: 1
Patient 99268, V86: 1.0
Patient 99268, V45: 1
Patient 99268, V10: 1
Patient 99268, 530: 1
Patient 992

Patient 99439, 428: 1
Patient 99439, 584: 1
Patient 99439, 428: 1
Patient 99439, 584: 1
Patient 99439, 276: 1
Patient 99439, 599: 1
Patient 99439, 348: 1
Patient 99439, 486: 1
Patient 99439, 250: 1
Patient 99439, 428: 1
Patient 99439, 416: 1
Patient 99439, 438: 1
Patient 99439, V45: 1
Patient 99439, V10: 1
Patient 99439, 437: 1
Patient 99439, 290: 1
Patient 99439, 728: 1
Patient 99439, 438: 1
Patient 99439, 327: 1
Patient 99439, 496: 1
Patient 99439, 780: 1
Patient 99439, 427: 1
Patient 99439, 585: 1
Patient 99439, 585: 1
Patient 99439, 427: 1
Patient 99439, 294: 1
Patient 99439, V45: 1
Patient 99439, 327: 1
Patient 99439, 438: 1
Patient 99439, 401: 1
Patient 99439, 294: 1
Patient 99439, 041: 1
Patient 99439, 287: 1
Patient 99439, 414: 1
Patient 99439, 276: 1
Patient 99439, 348: 1
Patient 99439, 584: 1
Patient 99439, 428: 1
Patient 99439, 496: 1
Patient 99439, 250: 1
Patient 99439, 414: 1
Patient 99439, V10: 1
Patient 99439, V45: 1
Patient 99439, 428: 1
Patient 99439, V12: 1
Patient 99

Patient 99660, 493: 1
Patient 99660, 403: 1
Patient 99660, 585: 1
Patient 99660, 424: 1
Patient 99660, 278: 1
Patient 99660, 327: 1
Patient 99660, V45: 1
Patient 99660, 965: 1
Patient 99660, V58: 1
Patient 99660, 780: 1
Patient 99660, 250: 1
Patient 99660, V45: 1
Patient 99660, 428: 1
Patient 99660, 244: 1
Patient 99660, E855: 1
Patient 99660, E850: 1
Patient 99660, 966: 1
Patient 99660, 412: 1
Iteration: 10291
Patient 99714, 365: 1
Patient 99714, 333: 1
Patient 99714, 244: 1
Patient 99714, 414: 1
Patient 99714, 782: 1
Patient 99714, V58: 1
Patient 99714, 427: 1
Patient 99714, 790: 1
Patient 99714, 278: 1
Patient 99714, 250: 1
Patient 99714, 599: 1
Patient 99714, V58: 1
Patient 99714, 272: 1
Patient 99714, 401: 1
Patient 99714, 458: 1
Patient 99714, 426: 1
Patient 99714, 996: 1
Patient 99714, 427: 1
Patient 99714, 327: 1
Patient 99714, V15: 1
Patient 99714, 794: 1
Patient 99714, V14: 1
Iteration: 10292
Patient 99756, 287: 1
Patient 99756, 276: 1
Patient 99756, 276: 1
Patient 99756, 584

Patient 99901, 599: 1
Patient 99901, 428: 1
Patient 99901, 276: 1
Patient 99901, 311: 1
Iteration: 10309
Patient 99903, 747: 1
Patient 99903, 401: 1
Patient 99903, 305: 1
Patient 99903, 250: 1
Patient 99903, V64: 1
Iteration: 10310
Patient 99913, 401: 1
Patient 99913, 780: 1
Patient 99913, 788: 1
Patient 99913, 427: 1
Patient 99913, 424: 1
Patient 99913, 780: 1
Patient 99913, 348: 1
Patient 99913, 414: 1
Patient 99913, 250: 1
Patient 99913, 440: 1
Patient 99913, V58: 1
Patient 99913, 272: 1
Iteration: 10311
Patient 99928, 250: 1
Patient 99928, V15: 1
Patient 99928, 311: 1
Patient 99928, 272: 1
Patient 99928, V58: 1
Iteration: 10312
Patient 99938, 250: 1
Patient 99938, 733: 1
Patient 99938, 723: 1
Patient 99938, V13: 1
Patient 99938, 501: 1
Patient 99938, 585: 1
Patient 99938, 401: 1
Patient 99938, 428: 1
Patient 99938, 276: 1
Patient 99938, 424: 1
Patient 99938, 414: 1
Patient 99938, 428: 1
Patient 99938, 285: 1
Iteration: 10313
Patient 99955, 432: 1
Patient 99955, 348: 1
Patient 99955

In [81]:
p3

SUBJECT_ID GENDER                                          DIAGNOSES  \
0              13      F  ['Pure hypercholesterolemia', 'Unspecified ess...   
1              18      M  ['Pure hypercholesterolemia', 'Right bundle br...   
2              20      F  ['Coronary atherosclerosis of native coronary ...   
3              21      M  ['Abscess of liver', 'Intestinal infection due...   
4              24      M  ['Diabetes mellitus without mention of complic...   
5              25      M  ['Unspecified essential hypertension', 'Corona...   
6              28      M  ['Other isolated or specific phobias', nan, 'P...   
7              35      F  ['Osteoarthrosis, unspecified whether generali...   
8              37      M  ['Subendocardial infarction, initial episode o...   
9              55      F  ['Occlusion and stenosis of carotid artery wit...   
10             59      F  ['Hypotension, unspecified', 'Urinary tract in...   
11             75      F  ['Diabetes mellitus without mention of complic...   
12             83      F  ['Hypertensive chronic kidney disease, unspeci...   
13            117      F  ['Acute posthemorrhagic anemia', 'Cirrhosis of...   
14            123      M  ['Unspecified essential hypertension', 'Acute ...   
15            130      M  ['Pure hypercholesterolemia', 'Polyneuropathy ...   
16            135      M  ['Diabetes mellitus without mention of complic...   
17            137      M  ['Personal history of tobacco use', 'Percutane...   
18            141      M  ['Diabetes with ketoacidosis, type I [juvenile...   
19            157      M  ['Hypopotassemia', nan, 'Unspecified essential...   
20            173      F  ['Unspecified sleep apnea', 'Coronary atherosc...   
21            184      M  [nan, 'Pneumonia, organism unspecified', nan, ...   
22            186      F  ['Esophageal varices with bleeding', 'Pneumoni...   
23            188      M  ['Surgical operation with transplant of whole ...   
24            191      M  ['Iron deficiency anemia secondary to blood lo...   
25            192      M  ['Peripheral vascular disease, unspecified', '...   
26            199      M  ['Polyneuropathy in diabetes', 'Congestive hea...   
27            205      F  ['Old myocardial infarction', 'Diabetes mellit...   
28            209      M  ['Hyperpotassemia', 'Diabetes with other speci...   
29            210      F  ['Esophageal reflux', 'Other and unspecified h...   
...           ...    ...                                                ...   
10288       99629      M  ['Esophageal reflux', 'Other and unspecified h...   
10289       99650      F  ['Anemia of other chronic disease', 'Extrinsic...   
10290       99660      F  [nan, 'Chronic kidney disease, Stage IV (sever...   
10291       99714      M  ['Unspecified glaucoma', 'Essential and other ...   
10292       99756      M  ['Thrombocytopenia, unspecified', 'Hyposmolali...   
10293       99776      M  ['Encephalopathy, unspecified', 'Unspecified p...   
10294       99791      M  ['Calculus of bile duct with other cholecystit...   
10295       99802      F  ['Chronic airway obstruction, not elsewhere cl...   
10296       99806      M  ['Other postoperative infection', 'Cellulitis ...   
10297       99809      M  ['Coronary atherosclerosis of native coronary ...   
10298       99810      M  ['Urinary complications, not elsewhere classif...   
10299       99814      F  ['Other toe(s) amputation status', 'Urinary tr...   
10300       99819      M  ['Other and unspecified hyperlipidemia', 'Card...   
10301       99830      M  ['Personal history of sudden cardiac arrest', ...   
10302       99863      M  ['Other and unspecified hyperlipidemia', 'Acut...   
10303       99864      M  ['Chronic kidney disease, Stage III (moderate)...   
10304       99870      F  ['Obstructive sleep apnea (adult)(pediatric)',...   
10305       99893      M  ['Syncope and collapse', 'Accidental fall from...   
10306       99897      M  ['Polyneuropathy in diabetes', 

In [82]:
p3.to_csv(r'../data/diabetes_binary.csv')

In [5]:
diabetes = pd.read_csv('../data/diabetes_matrix.csv')

In [6]:
diabetes.columns

Index(['Unnamed: 0', 'SUBJECT_ID', 'LOS', 'HOSPITALIZATION', 'ELECTIVE',
       'EMERGENCY', 'NEWBORN', 'URGENT', 'Government', 'Medicaid',
       ...
       'NATIVE HAWAIIAN OR OTHER PACIFIC ISLANDER',
       'HISPANIC/LATINO - CENTRAL AMERICAN (OTHER)', 'ASIAN - JAPANESE',
       'ASIAN - THAI', 'HISPANIC/LATINO - HONDURAN', 'HISPANIC/LATINO - CUBAN',
       'MIDDLE EASTERN', 'ASIAN - OTHER', 'HISPANIC/LATINO - MEXICAN',
       'AMERICAN INDIAN/ALASKA NATIVE FEDERALLY RECOGNIZED TRIBE'],
      dtype='object', length=931)

In [9]:
diabetes.drop(columns = ['', '', ])

TypeError: bad operand type for unary -: 'str'